In [4]:
%load_ext autoreload
%autoreload 2

import numpy as np
import pandas as pd
import json
import yaml
import ast
from pathlib import Path

import torch
from torch.utils.data import Dataset, DataLoader, ConcatDataset
from fusanet_utils.datasets.simulated import SimulatedPoliphonic
from fusanet_utils.datasets.fusa import FUSA_dataset
from sed_visualizer import create_sed_gui

#experiment_path = Path('../../experiments/Poliphonic-PANN-sed-pink-noise/')
experiment_path = Path('../../experiments/Poliphonic-PANN-sed-no-pretrained')
print(experiment_path)

categories = json.load(open(str(experiment_path / 'index_to_name.json')))
fusa_taxonomy = json.load(open('../../fusa_taxonomy.json'))
taxonony_translator = {label: key for key, value in fusa_taxonomy.items() for label in value['SPASS']}
translated_categories = {key: taxonony_translator[value] for key, value in categories.items()}  

model = torch.load(str(experiment_path / 'model.pt'))
model.eval()
params = yaml.safe_load(open(str(experiment_path / 'params.yaml')))

class Vicente(Dataset):
    def __init__(self, categories):
        self.file_paths = []
        self.meta = pd.read_csv('../../datasets/Vicente/Metadata.csv', 
                                encoding='latin-1', sep=';', header=0, comment='#', parse_dates=[4])
        self.labels = []
        self.folder = []
        for file in Path('../../datasets/Vicente/').rglob('*.wav'):
            tag = self.match_ids(file)["Tag 1"].apply(lambda x: x.split(':')[0] if isinstance(x, str) else None)
            if len(tag) == 0:
                #print(id, file, tag)
                continue
            self.labels.append(tag.item())
            self.file_paths.append(file)
            self.folder.append(file.parent.stem)
        self.categories = categories
    
    def match_ids(self, file_name):
        id = file_name.stem
        if id[-3:] == '(1)':
            id = id[:-3]
        return self.meta.loc[self.meta['Id'] == id]         
        
    def __getitem__(self, idx):
        return self.file_paths[idx], 'dog'
        #return self.file_paths[idx], self.labels[idx]
    
    def __len__(self):
        return len(self.file_paths)
    
dataset = Vicente(list(categories.values()))
fusa_dataset = FUSA_dataset(ConcatDataset([dataset]), params)
#fusa_dataset = FUSA_dataset(ConcatDataset([SimulatedPoliphonic('../../', mini=False, external=True)]), params)

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload
../../experiments/Poliphonic-PANN-sed-no-pretrained


In [5]:
create_sed_gui(fusa_dataset[7], model, params, fusa_dataset.categories)

Column
    [0] Spacer(height=10)
    [1] IntSlider(end=6001, name='Time')
    [2] HoloViews(Layout)
    [3] ParamFunction(function)

In [2]:
create_sed_gui(fusa_dataset[7], model, params, fusa_dataset.categories)

Column
    [0] Spacer(height=10)
    [1] IntSlider(end=6001, name='Time')
    [2] HoloViews(Layout)
    [3] ParamFunction(function)